# [Monopoly Odds](https://projecteuler.net/problem=84)

We could solve this problem by actually simulating moving across a Monopoly board with dice rolls and card decks, but with a little creativity, we can model it more precisely with a [Markov chain](https://en.wikipedia.org/wiki/Markov_chain). But before we get to any of that, let's enumerate the labels of the squares so we don't have to count so much!

In [1]:
squares = {s: idx for (idx, s) in enumerate(("GO", "A1", "CC1", "A2", "T1", "R1", "B1", "CH1", "B2", "B3", "JAIL", "C1", "U1", "C2", "C3", "R2", "D1", "CC2", "D2", "D3", "FP", "E1", "CH2", "E2", "E3", "R3", "F1", "F2", "U2", "F3", "G2J", "G1", "G2", "CC3", "G3", "R4", "CH3", "H1", "T2", "H2"))}

To construct the [stochastic matrix](https://en.wikipedia.org/wiki/Stochastic_matrix) of the Markov chain, we'll start simple by ignoring the special rules for:
* rolling three doubles in a row
* landing on Go To Jail
* landing on community chest
* landing on chance

Then, we'll consider each of these special rules one at a time and adjust the transition probabilities accordingly. Each entry $(i,j)$ in the matrix will ultimately represent the probability of ending in square $j$ after starting a turn in square $i$.

In [2]:
P = matrix(QQ, 40, 40, sparse=True)

Here, we'll construct a dictionary of every two-dice roll and their probabilities.

In [3]:
die_sides = 4
dice_dist = {(p, q): 1/die_sides^2 for p in range(1, die_sides + 1) for q in range(1, die_sides + 1)}

Here's where we compute the basic probabilities for landing on each square, without the special rules:

In [4]:
for start in range(0, 40):
    for ((p, q), prob) in dice_dist.items():
        roll = p + q
        P[start, (start + roll) % 40] += prob

## Rolling doubles

The first special rule we'll consider is going to jail after three consecutive rolls of doubles. To model this, we'll make three states for each square to capture the number of consecutive doubles that have been rolled (0, 1, or 2). This will triple both the number of rows and number of columns in the transition matrix.

If you don't roll a double, you'll transition to one of the states represented in the first 40 columns. These transitions have the same probabilities as the simple matrix $P$ we constructed above (at least for now).

In [5]:
Q = matrix(QQ, 120, 120, sparse=True)
Q[:40, :40] = P
Q[40:80, :40] = P
Q[80:120, :40] = P

When there's a double, you transition to the next double state in the sequence (in other words, you move 40 columns over). When the third double is rolled, [right to jail](https://www.youtube.com/watch?v=eiyfwZVAzGw). This also reduces the probabilities in the first 40 columns, so they don't stay exact duplicates of $P$.

In [6]:
for start in range(0, 40):
    for ((p, q), prob) in dice_dist.items():
        if p == q:
            roll = p + q
            end = (start + roll) % 40
            
            Q[start, end + 40] += prob
            Q[start + 40, end + 80] += prob
            Q[start + 80, squares['JAIL']] += prob
            
            Q[start, end] -= prob
            Q[start + 40, end] -= prob
            Q[start + 80, end] -= prob

## Go To Jail

Next, if we land on Go To Jail, the end result is landing on Jail (duh). There's a nested loop here so that we adjust the probabilities for each possible transition between all our duplicated doubles states, as well.

In [7]:
for roll in range(2, 2 * die_sides + 1):
    for (s, t) in ((0, 0), (0, 40), (40, 0), (40, 80), (80, 0)):
        init = (squares['G2J'] - roll) % 40 + s

        Q[init, squares['JAIL'] + t] += Q[init, squares['G2J'] + t]
        Q[init, squares['G2J'] + t] = 0

## Community chest

Next, we'll handle the probability that we move to either Go or Jail after landing on community chest. We make this adjustment by applying [conditional probability](https://en.wikipedia.org/wiki/Conditional_probability).

(A technical note: since a Markov chain requires memorylessness, it would be impractical to model the true nature of the community chest and chance decks (shuffled at the beginning, then repeating in a loop). Instead, we'll assume that the decks are shuffled before each draw, effectively making them [uniform random variables](https://en.wikipedia.org/wiki/Discrete_uniform_distribution). This won't be an issue for this problem since we don't need the exact probabilities of the squares.)

In [8]:
for cc in (squares['CC1'], squares['CC2'], squares['CC3']):
    for roll in range(2, 2 * die_sides + 1):
        for (s, t) in ((0, 0), (0, 40), (40, 0), (40, 80), (80, 0)):
            init = (cc - roll) % 40 + s
            cc_prob = Q[init, cc + t]

            # handle moving straight to new square
            Q[init, squares['GO'] + t] += cc_prob * 1/16
            Q[init, squares['JAIL'] + t] += cc_prob * 1/16

            # reduce community chest space's probability
            Q[init, cc + t] *= 14/16

## Chance

Similarly to above, we adjust for drawing from chance, which is a little more complicated, since there are also cases that depend on the specific chance space we landed on.

In [9]:
for ch in (squares['CH1'], squares['CH2'], squares['CH3']):
    for roll in range(2, 2 * die_sides + 1):
        for (s, t) in ((0, 0), (0, 40), (40, 0), (40, 80), (80, 0)):
            init = (ch - roll) % 40 + s
            ch_prob = Q[init, ch + t]

            # handle moving straight to new square
            for sq in ('GO', 'R1', 'JAIL', 'C1', 'E3', 'H2'):
                Q[init, squares[sq] + t] += ch_prob * 1/16

            # handle moving to the *next* railroad/utility
            if ch == squares['CH1']:
                Q[init, squares['R2'] + t] += ch_prob * 2/16
                Q[init, squares['U1'] + t] += ch_prob * 1/16
            elif ch == squares['CH2']:
                Q[init, squares['R3'] + t] += ch_prob * 2/16
                Q[init, squares['U2'] + t] += ch_prob * 1/16
            elif ch == squares['CH3']:
                Q[init, squares['R1'] + t] += ch_prob * 2/16
                Q[init, squares['U1'] + t] += ch_prob * 1/16

            # handle moving three squares back
            Q[init, ch - 3 + t] += ch_prob * 1/16

            # reduce chance space's probability
            Q[init, ch + t] *= 6/16

## Finding the stationary distribution

As a sanity check, we can make sure all of the entries of the matrix are nonnegative and that all the rows sum to 1.

In [10]:
assert all(x >= 0 for row in Q for x in row)
assert all(x == 1 for x in sum(Q.T))

Now with all of the adjustments for special rules in place, we can solve the problem by finding the chain's stationary distribution, which is an [eigenvector](https://en.wikipedia.org/wiki/Eigenvalues_and_eigenvectors) of the stochastic matrix with eigenvalue 1. To find this eigenvector, we'll first find the basis vector of the [kernel](https://w.wiki/EoP5) of $Q - I$ (where $I$ is the identity matrix), with the help of SageMath.

In [11]:
b = (Q - identity_matrix(120)).kernel().basis()[0]

Since each square is represented by three states, we want to sum each triplet to get the total probability for each square.

In [12]:
v = sum(matrix(QQ, 3, 40, b))

With this vector found, we just need to normalize it so the entries sum to 1 - we can do this with the 1-norm, otherwise known as the [Manhattan norm](https://en.wikipedia.org/wiki/Taxicab_geometry).

In [13]:
pi = v.normalized(1)

Then we'll sort by highest probability.

In [14]:
sorted(enumerate(pi.n()), key=lambda x: x[1], reverse=True)

[(10, 0.0701408235247207),
 (15, 0.0361487100050623),
 (24, 0.0328724475541427),
 (16, 0.0322584962091447),
 (25, 0.0310964093466631),
 (19, 0.0306062292541469),
 (21, 0.0304867096651446),
 (20, 0.0299664869236993),
 (23, 0.0299370269427328),
 (18, 0.0297290718671866),
 (5, 0.0290016101756835),
 (14, 0.0288235313851932),
 (28, 0.0285344599840671),
 (31, 0.0281227577909694),
 (0, 0.0278137848332617),
 (29, 0.0275205747552836),
 (17, 0.0271550379206804),
 (26, 0.0264655804498234),
 (32, 0.0258238774287566),
 (27, 0.0255174128929372),
 (13, 0.0251599001514243),
 (39, 0.0247949649359000),
 (11, 0.0244402810295771),
 (12, 0.0241521076809198),
 (4, 0.0228303231805554),
 (33, 0.0220537515544996),
 (34, 0.0219893556241630),
 (37, 0.0212205690768340),
 (8, 0.0211429239372672),
 (9, 0.0209948500526884),
 (6, 0.0209206861048968),
 (38, 0.0208293527278273),
 (3, 0.0203131015847667),
 (35, 0.0198361718493843),
 (1, 0.0176178373964372),
 (2, 0.0167938454532514),
 (22, 0.0112454467024504),
 (36, 0.00

This gives our top squares as 10 (JAIL), 15 (R2), and 24 (E3).

#### Copyright (C) 2025 filifa

This work is licensed under the [Creative Commons Attribution-ShareAlike 4.0 International license](https://creativecommons.org/licenses/by-sa/4.0/) and the [BSD Zero Clause license](https://spdx.org/licenses/0BSD.html).